In [1]:
import h3
import folium

geoJson = {
    'type': 'Polygon',
    'coordinates': [
        [
            [-32.780366, -60.442793],
            [-32.739600, -60.920334],
            [-33.129155, -60.946906],
            [-33.133946, -60.265462]
        ],
    ]
}

polyline = geoJson['coordinates'][0]
polyline.append(polyline[0])
lat = [p[0] for p in polyline]
lng = [p[1] for p in polyline]
m = folium.Map(location=[sum(lat)/len(lat), sum(lng)/len(lng)], zoom_start=13, tiles='cartodbpositron')
my_PolyLine=folium.PolyLine(locations=polyline, weight=8, color="green")
m.add_child(my_PolyLine)

hexagons = list(h3.polyfill(geoJson, 8))
polylines = []
lat = []
lng = []
for hex in hexagons:
    polygons = h3.h3_set_to_multi_polygon([hex], geo_json=False)
    # flatten polygons into loops.
    outlines = [loop for polygon in polygons for loop in polygon]
    polyline = [outline + [outline[0]] for outline in outlines][0]
    lat.extend(map(lambda v: v[0], polyline))
    lng.extend(map(lambda v: v[1], polyline))
    polylines.append(polyline)

for polyline, hex_id in zip(polylines, hexagons):
    my_PolyLine = folium.PolyLine(locations=polyline, weight=1, color='red')
    m.add_child(my_PolyLine)

    # Calculate the center of the hexagon
    center_lat, center_lng = h3.h3_to_geo(hex_id)

    # Add a marker with the hex ID at the center of the hexagon
    folium.map.Marker(
        location=[center_lat, center_lng],

        icon=folium.DivIcon(
            icon_size=(30, 30),  # Adjust the size as needed
            icon_anchor=(15, 15),
            html=f'<div style="font-size: 15px; text-align: center;">{hex_id}</div>'
        )
    ).add_to(m)

display(m)